# SARIMAX forecasting on PV

#### Import data

In [280]:
import warnings
warnings.filterwarnings("ignore")
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import pandas as pd
import numpy as np

from statsmodels.graphics.tsaplots import plot_acf, plot_pacf
from statsmodels.tsa.stattools import acf, pacf
from sktime.forecasting.arima import ARIMA

import DataRetriever as dr

retriever = dr.DataRetriever()
#year1 = retriever.get_data("All-Subsystems-hour-Year1.pkl")
year2 = retriever.get_data("All-Subsystems-hour-Year2.pkl")
year2

Timestamp  Load_LatentHeatWaterVolume  \
Timestamp                                                             
2015-02-01 00:00:00 2015-02-01 00:00:00                    0.060105   
2015-02-01 01:00:00 2015-02-01 01:00:00                    0.131439   
2015-02-01 02:00:00 2015-02-01 02:00:00                    0.194187   
2015-02-01 03:00:00 2015-02-01 03:00:00                    0.258256   
2015-02-01 04:00:00 2015-02-01 04:00:00                    0.322324   
...                                 ...                         ...   
2016-01-31 19:00:00 2016-01-31 19:00:00                    1.472255   
2016-01-31 20:00:00 2016-01-31 20:00:00                    1.546231   
2016-01-31 21:00:00 2016-01-31 21:00:00                    1.617565   
2016-01-31 22:00:00 2016-01-31 22:00:00                    1.688899   
2016-01-31 23:00:00 2016-01-31 23:00:00                    1.763535   

                     Load_RefrigeratorTemp  Load_StatusBA1Lights  \
Timestamp                                                          
2015-02-01 00:00:00               4.957915                   0.0   
2015-02-01 01:00:00               4.904702                   0.0   
2015-02-01 02:00:00               5.054887                   0.0   
2015-02-01 03:00:00               4.991525                   0.0   
2015-02-01 04:00:00               5.040868                   0.0   
...                                    ...                   ...   
2016-01-31 19:00:00               4.810046                   0.0   
2016-01-31 20:00:00               4.917617                   0.0   
2016-01-31 21:00:00               4.820712                   0.0   
2016-01-31 22:00:00               4.945030                   0.0   
2016-01-31 23:00:00               4.826671                   0.0   

                     Load_StatusKitchenLightsA  Load_StatusKitchenLightsB  \
Timestamp                                                                   
2015-02-01 00:00:00                   0.000000                   0.000000   
2015-02-01 01:00:00                   0.000000                   0.000000   
2015-02-01 02:00:00                   0.000000                   0.000000   
2015-02-01 03:00:00                   0.000000                   0.000000   
2015-02-01 04:00:00                   0.000000                   0.000000   
...                                        ...                        ...   
2016-01-31 19:00:00                   0.750000                   0.750000   
2016-01-31 20:00:00                   0.750000                   0.750000   
2016-01-31 21:00:00                   1.000000                   1.000000   
2016-01-31 22:00:00                   0.483333                   0.483333   
2016-01-31 23:00:00                   0.000000                   0.000000   

                     Load_StatusKitchenLightsC  Load_StatusDRLights  \
Timestamp                                                             
2015-02-01 00:00:00                   0.000000             0.000000   
2015-02-01 01:00:00                   0.000000             0.000000   
2015-02-01 02:00:00                   0.000000             0.000000   
2015-02-01 03:00:00                   0.000000             0.000000   
2015-02-01 04:00:00                   0.000000             0.000000   
...                                        ...                  ...   
2016-01-31 19:00:00                   0.750000             0.766667   
2016-01-31 20:00:00                   0.750000             0.483333   
2016-01-31 21:00:00                   1.000000             0.000000   
2016-01-31 22:00:00                   0.483333             0.000000   
2016-01-31 23:00:00                   0.000000             0.000000   

                     Load_StatusLRLights3  Load_StatusEntryHallLights  ...  \
Timestamp                                                              ...   
2015-02-01 00:00:00              0.000000                         0.0  ...   
2015-02-01 01:00:00              0.000000                    

In [281]:
# gen_year1 = year1[year1["PV_Watts3PhTotalW3PhT1"].isna() == False]
# gen_year1 = gen_year1[gen_year1["PV_Watts3PhTotalW3PhT2"].isna() == False] #There are 87 rows with NaN values.
#
# print(f"A total of {len(year1) - len(gen_year1)} rows have been dropped since they have NaN values.")
#
# gen_year1["Generated Energy"] = (gen_year1["PV_Watts3PhTotalW3PhT1"].to_numpy() + gen_year1["PV_Watts3PhTotalW3PhT2"].to_numpy())
# gen_year1 = gen_year1[["Generated Energy"]] / 1e3 #Convert Wh to kWh
# gen_year1

In [282]:
gen_year2 = year2[year2["PV_Watts3PhTotalW3PhT1"].isna() == False]
gen_year2 = gen_year2[gen_year2["PV_Watts3PhTotalW3PhT2"].isna() == False] #There are 87 rows with NaN values.

print(f"A total of {len(year2) - len(gen_year2)} rows have been dropped since they have NaN values.")

gen_year2["Generated Energy"] = (gen_year2["PV_Watts3PhTotalW3PhT1"].to_numpy() + gen_year2["PV_Watts3PhTotalW3PhT2"].to_numpy())
gen_year2 = gen_year2[["Generated Energy"]] / 1e3 #Convert Wh to kWh
gen_year2

A total of 87 rows have been dropped since they have NaN values.


Generated Energy
Timestamp                            
2015-02-01 00:00:00          0.018496
2015-02-01 01:00:00          0.018332
2015-02-01 02:00:00          0.018385
2015-02-01 03:00:00          0.018502
2015-02-01 04:00:00          0.018524
...                               ...
2016-01-31 19:00:00          0.017710
2016-01-31 20:00:00          0.017940
2016-01-31 21:00:00          0.018149
2016-01-31 22:00:00          0.018209
2016-01-31 23:00:00          0.018283

[8673 rows x 1 columns]

In [283]:
# gen_df = pd.concat([gen_year1, gen_year2])
# gen_df

In [284]:
gen_df = gen_year2

gen_df = gen_df.resample('h').sum()
gen_df

Generated Energy
Timestamp                            
2015-02-01 00:00:00          0.018496
2015-02-01 01:00:00          0.018332
2015-02-01 02:00:00          0.018385
2015-02-01 03:00:00          0.018502
2015-02-01 04:00:00          0.018524
...                               ...
2016-01-31 19:00:00          0.017710
2016-01-31 20:00:00          0.017940
2016-01-31 21:00:00          0.018149
2016-01-31 22:00:00          0.018209
2016-01-31 23:00:00          0.018283

[8760 rows x 1 columns]

In [285]:
fig = go.Figure(go.Scattergl(
    x = gen_df.index,
    y = gen_df["Generated Energy"]
))

fig.show()

#### Train, Validation and Test data

In [286]:
#Doing the training, validation and test splits now so they can be used for forecasting later.

In [287]:
exog_attributes = pd.DataFrame(year2['PV_PVInsolationHArray'].resample('h').sum()) # If we want exogenous attributes in the model as well.

X = pd.merge(gen_df, exog_attributes, how='left', on=gen_df.index)
X.drop(columns=['key_0'], inplace=True)
X.index = gen_df.index
#X.drop(columns=['1dif', '2dif', '3dif', 'Seasonal Difference'], inplace=True)
X

Generated Energy  PV_PVInsolationHArray
Timestamp                                                   
2015-02-01 00:00:00          0.018496               0.057408
2015-02-01 01:00:00          0.018332               0.060286
2015-02-01 02:00:00          0.018385               0.058811
2015-02-01 03:00:00          0.018502               0.058865
2015-02-01 04:00:00          0.018524               0.059288
...                               ...                    ...
2016-01-31 19:00:00          0.017710               0.059872
2016-01-31 20:00:00          0.017940               0.059688
2016-01-31 21:00:00          0.018149               0.058976
2016-01-31 22:00:00          0.018209               0.059878
2016-01-31 23:00:00          0.018283               0.058991

[8760 rows x 2 columns]

In [288]:
prediction_range = 24 * 3  #Three days

In [289]:
test_df = X[len(X) - prediction_range:]
test_df

Generated Energy  PV_PVInsolationHArray
Timestamp                                                   
2016-01-29 00:00:00          0.018250               0.057477
2016-01-29 01:00:00          0.018189               0.056396
2016-01-29 02:00:00          0.018158               0.057628
2016-01-29 03:00:00          0.018049               0.056413
2016-01-29 04:00:00          0.018243               0.058013
...                               ...                    ...
2016-01-31 19:00:00          0.017710               0.059872
2016-01-31 20:00:00          0.017940               0.059688
2016-01-31 21:00:00          0.018149               0.058976
2016-01-31 22:00:00          0.018209               0.059878
2016-01-31 23:00:00          0.018283               0.058991

[72 rows x 2 columns]

In [290]:
X.drop(test_df.index, inplace=True)

validation_df = X[len(X) - prediction_range:]
validation_df

Generated Energy  PV_PVInsolationHArray
Timestamp                                                   
2016-01-26 00:00:00          0.000000               0.000000
2016-01-26 01:00:00          0.000000               0.000000
2016-01-26 02:00:00          0.000000               0.000000
2016-01-26 03:00:00          0.000000               0.000000
2016-01-26 04:00:00          0.000000               0.000000
...                               ...                    ...
2016-01-28 19:00:00          0.017729               0.057850
2016-01-28 20:00:00          0.017849               0.056320
2016-01-28 21:00:00          0.017882               0.057342
2016-01-28 22:00:00          0.018000               0.057909
2016-01-28 23:00:00          0.018138               0.056369

[72 rows x 2 columns]

In [291]:
train_df = X[:len(X)-prediction_range]
train_df

Generated Energy  PV_PVInsolationHArray
Timestamp                                                   
2015-02-01 00:00:00          0.018496               0.057408
2015-02-01 01:00:00          0.018332               0.060286
2015-02-01 02:00:00          0.018385               0.058811
2015-02-01 03:00:00          0.018502               0.058865
2015-02-01 04:00:00          0.018524               0.059288
...                               ...                    ...
2016-01-25 19:00:00          0.014773               0.058367
2016-01-25 20:00:00          0.000000               0.057008
2016-01-25 21:00:00          0.000000               0.000000
2016-01-25 22:00:00          0.000000               0.000000
2016-01-25 23:00:00          0.000000               0.000000

[8616 rows x 2 columns]

#### Check if PV is stationary + Differencing

In [292]:
from statsmodels.tsa.stattools import adfuller

ADF_test = adfuller(gen_df["Generated Energy"])

print(f"The p-value from the Augmented Dickey-Fuller test is {ADF_test[1]}. \n This suggest that the TS is stationary, and d=0.")

The p-value from the Augmented Dickey-Fuller test is 4.569102377280105e-19. 
 This suggest that the TS is stationary, and d=0.


In [293]:
#However according to https://people.duke.edu/~rnau/arimrule.htm, we need to check the autocorrelations as well.

#autocorrelation_no_difference = plot_acf(gen_df["Generated Energy"].dropna())

In [294]:
# Doing the differencing for fun

gen_df['1dif'] = gen_df["Generated Energy"] - gen_df["Generated Energy"].shift(1)
gen_df['2dif'] = gen_df["Generated Energy"] - gen_df["Generated Energy"].shift(2)
gen_df['3dif'] = gen_df["Generated Energy"] - gen_df["Generated Energy"].shift(3)

# gen_df

#### Determine order of autoregressive terms (p) and moving average terms (q)

In [295]:
acf_values, acf_conf = acf(gen_df['Generated Energy'].dropna(), alpha=0.05)

for i in range(len(acf_values)):
    acf_conf[i] = acf_conf[i] - acf_values[i]

acf_conf = pd.DataFrame(acf_conf, columns=['Upper', 'Lower'])

fig = go.Figure(go.Bar(
    y = acf_values
))

fig.add_trace(go.Scatter(
    x = list(acf_conf.index) + list(acf_conf.index[::-1]),
    y = list(acf_conf['Upper']) + list(acf_conf['Lower'][::-1]),
    fill='toself',
    fillcolor='rgba(0,100,80,0.2)',
    line=dict(color='rgba(255,255,255,0)'),
    hoverinfo="skip",
    showlegend=False
))

fig.update_yaxes(title="Autocorrelation", range=[-1, 1])
fig.update_xaxes(title="Lag")

fig.show()

#autocorrelation_no_difference = plot_acf(gen_df["Generated Energy"].dropna())
# autocorrelation_first_difference = plot_acf(gen_df["1dif"].dropna())

In [296]:
pacf_values, pacf_conf = pacf(gen_df['Generated Energy'].dropna(), alpha=0.05)

for i in range(len(pacf_values)):
    pacf_conf[i] = pacf_conf[i] - pacf_values[i]

pacf_conf = pd.DataFrame(pacf_conf, columns=['Upper', 'Lower'])

fig = go.Figure(go.Bar(
    y = pacf_values
))

fig.add_trace(go.Scatter(
    x = list(pacf_conf.index) + list(pacf_conf.index[::-1]),
    y = list(pacf_conf['Upper']) + list(pacf_conf['Lower'][::-1]),
    fill='toself',
    fillcolor='rgba(0,100,80,0.2)',
    line=dict(color='rgba(255,255,255,0)'),
    hoverinfo="skip",
    showlegend=False
))

fig.update_yaxes(title="Partial Autocorrelation", range=[-1, 1])
fig.update_xaxes(title="Lag")

fig.show()

#partialautocorrelation_no_difference = plot_pacf(gen_df['Generated Energy'].dropna())
#partialautocorrelation_first_difference = plot_pacf(gen_df['1dif'].dropna())
#partialautocorrelation_second_difference = plot_pacf(gen_df['2dif'].dropna())
#partialautocorrelation_third_difference = plot_pacf(gen_df['3dif'].dropna())

In [297]:
print(f"The sinusoidal tendency of the ACF plot suggests that the parameters should be ARIMA(4, 0, 0)")

The sinusoidal tendency of the ACF plot suggests that the parameters should be ARIMA(4, 0, 0)


#### ARIMA(4, 0, 0)

In [298]:
from statsmodels.tsa.statespace.sarimax import SARIMAX

def arimamodel(*, training_data, trend='c', p, d, q, P=0, D=0, Q=0, m=0,):

    model = SARIMAX(training_data, trend=trend, order=(p, d, q), seasonal_order=(P, D, Q, m))
    fitted_model = model.fit()

    return fitted_model

def arima_forecast(data, fitted_model, *, start_index, end_index):

    data['Prediction'] = fitted_model.predict(start = start_index, end = end_index)

    predictions = fitted_model.get_forecast(end_index)
    #yhat = test.predicted_mean
    yhat_conf = predictions.conf_int(alpha=0.9)

    return data, yhat_conf


def plot_forecast(data, conf_interval, bands=True):

    fig = go.Figure(go.Scattergl(
        x = data.index,
        y = data['Generated Energy'],
        name = "Observed Values"
    ))

    fig.add_trace(go.Scattergl(
        x = data.index,
        y = data['Prediction'],
        name = "Predicted Values"
    ))

    if bands == True:
        fig.add_trace(go.Scattergl(
            x = conf_interval.index,
            y = conf_interval['lower Generated Energy'],
            name = "Lower Bound"
        ))

        fig.add_trace(go.Scattergl(
            x = conf_interval.index,
            y = conf_interval['upper Generated Energy'],
            name = "Upper Bound"
        ))

    fig.show()

In [299]:
model1 = arimamodel(training_data=train_df['Generated Energy'], trend='c', p=4, d=0, q=0)
model1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                               SARIMAX Results                                
==============================================================================
Dep. Variable:       Generated Energy   No. Observations:                 8616
Model:               SARIMAX(4, 0, 0)   Log Likelihood              -10385.704
Date:                Mon, 02 May 2022   AIC                          20783.407
Time:                        11:22:00   BIC                          20825.776
Sample:                    02-01-2015   HQIC                         20797.856
                         - 01-25-2016                                         
Covariance Type:                  opg                                         
==============================================================================
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
intercept      0.2671      0.019     13.932      0.000       0.230       0.305
ar.L1          1.2682      0.007    176.425      0.000       1.254       1.282
ar.L2         -0.2803      0.009    -32.235      0.000      -0.297      -0.263
ar.L3         -0.0041      0.011     -0.382      0.703      -0.025       0.017
ar.L4         -0.1514      0.008    -19.117      0.000      -0.167      -0.136
sigma2         0.6522      0.006    112.030      0.000       0.641       0.664
===================================================================================
Ljung-Box (L1) (Q):                   0.03   Jarque-Bera (JB):             34883.09
Prob(Q):                              0.86   Prob(JB):                         0.00
Heteroskedasticity (H):               0.68   Skew:                             0.79
Prob(H) (two-sided):                  0.00   Kurtosis:                        12.73
===================================================================================

Warnings:
[1] Covariance matrix calculated using the outer product of gradients (complex-step).
"""

In [300]:
forecast1, conf_int1 = arima_forecast(data=gen_df, fitted_model=model1, start_index=0, end_index=validation_df.index[-1])
forecast1

Generated Energy      1dif      2dif      3dif  \
Timestamp                                                             
2015-02-01 00:00:00          0.018496       NaN       NaN       NaN   
2015-02-01 01:00:00          0.018332 -0.000165       NaN       NaN   
2015-02-01 02:00:00          0.018385  0.000053 -0.000112       NaN   
2015-02-01 03:00:00          0.018502  0.000117  0.000170  0.000005   
2015-02-01 04:00:00          0.018524  0.000022  0.000139  0.000192   
...                               ...       ...       ...       ...   
2016-01-31 19:00:00          0.017710  0.000288 -0.038315 -0.716600   
2016-01-31 20:00:00          0.017940  0.000230  0.000518 -0.038084   
2016-01-31 21:00:00          0.018149  0.000208  0.000439  0.000727   
2016-01-31 22:00:00          0.018209  0.000060  0.000269  0.000499   
2016-01-31 23:00:00          0.018283  0.000074  0.000134  0.000343   

                     Prediction  
Timestamp                        
2015-02-01 00:00:00    1.593420  
2015-02-01 01:00:00    0.143705  
2015-02-01 02:00:00    0.209233  
2015-02-01 03:00:00    0.247685  
2015-02-01 04:00:00    0.282544  
...                         ...  
2016-01-31 19:00:00         NaN  
2016-01-31 20:00:00         NaN  
2016-01-31 21:00:00         NaN  
2016-01-31 22:00:00         NaN  
2016-01-31 23:00:00         NaN  

[8760 rows x 5 columns]

In [301]:
fig = go.Figure(go.Scattergl(
    x = train_df.index,
    y = train_df['Generated Energy'],
    name = "Training Data"
))

fig.add_trace(go.Scattergl(
    x = validation_df.index,
    y = validation_df['Generated Energy'],
    name = "Validation Data"
))

fig.add_trace(go.Scattergl(
    x = forecast1.index,
    #[validation_df.index[0]:validation_df.index[-1]].index,
    y = forecast1['Prediction'],
    #[validation_df.index[0]:validation_df.index[-1]],
    name = "Predicted Values"
))

# if bands == True:
#     fig.add_trace(go.Scattergl(
#         x = conf_interval.index,
#         y = conf_interval['lower Generated Energy'],
#         name = "Lower Bound"
#     ))
#
#     fig.add_trace(go.Scattergl(
#         x = conf_interval.index,
#         y = conf_interval['upper Generated Energy'],
#         name = "Upper Bound"
#     ))

fig.update_yaxes(title="Generated Energy [kWh]")

fig.show()

In [302]:
#plot_forecast(data=forecast[:validation_df.index[-1]], conf_interval=conf_int, bands=False)

## Seasonal ARIMA

#### Calculate seasonal difference

In [303]:
# Calculate the seasonal difference as a daily seasonality.
gen_df["Seasonal Difference"] = gen_df["Generated Energy"] - gen_df["Generated Energy"].shift(24)
gen_df

Generated Energy      1dif      2dif      3dif  \
Timestamp                                                             
2015-02-01 00:00:00          0.018496       NaN       NaN       NaN   
2015-02-01 01:00:00          0.018332 -0.000165       NaN       NaN   
2015-02-01 02:00:00          0.018385  0.000053 -0.000112       NaN   
2015-02-01 03:00:00          0.018502  0.000117  0.000170  0.000005   
2015-02-01 04:00:00          0.018524  0.000022  0.000139  0.000192   
...                               ...       ...       ...       ...   
2016-01-31 19:00:00          0.017710  0.000288 -0.038315 -0.716600   
2016-01-31 20:00:00          0.017940  0.000230  0.000518 -0.038084   
2016-01-31 21:00:00          0.018149  0.000208  0.000439  0.000727   
2016-01-31 22:00:00          0.018209  0.000060  0.000269  0.000499   
2016-01-31 23:00:00          0.018283  0.000074  0.000134  0.000343   

                     Prediction  Seasonal Difference  
Timestamp                                             
2015-02-01 00:00:00    1.593420                  NaN  
2015-02-01 01:00:00    0.143705                  NaN  
2015-02-01 02:00:00    0.209233                  NaN  
2015-02-01 03:00:00    0.247685                  NaN  
2015-02-01 04:00:00    0.282544                  NaN  
...                         ...                  ...  
2016-01-31 19:00:00         NaN             0.000077  
2016-01-31 20:00:00         NaN             0.000123  
2016-01-31 21:00:00         NaN             0.000199  
2016-01-31 22:00:00         NaN             0.000154  
2016-01-31 23:00:00         NaN             0.000120  

[8760 rows x 6 columns]

In [304]:
test = adfuller(gen_df["Seasonal Difference"].dropna())

print(f"The p value for the seasonal difference is {test[1]}. \nThis suggest D=0.")

The p value for the seasonal difference is 0.0. 
This suggest D=0.


In [305]:
fig = go.Figure(go.Scatter(
    x = gen_df.index,
    y = gen_df["Seasonal Difference"]
))

fig.update_yaxes(title="Generated Energy [kWh]")

fig.show()

### SAR and SMA terms

In [340]:
# autocorrelation_seasonal_difference = plot_acf(gen_df["Seasonal Difference"].dropna())
# partialautocorrelation_seasonal_difference = plot_pacf(gen_df['Seasonal Difference'].dropna())

seasonal_acf_values, seasonal_acf_conf = acf(gen_df['Seasonal Difference'].dropna(), nlags=168, alpha=0.05)
seasonal_pacf_values, seasonal_pacf_conf = pacf(gen_df['Seasonal Difference'].dropna(), nlags=168, alpha=0.05)

for i in range(len(seasonal_acf_values)):
    seasonal_acf_conf[i] = seasonal_acf_conf[i] - seasonal_acf_values[i]

seasonal_acf_conf = pd.DataFrame(seasonal_acf_conf, columns=['Upper', 'Lower'])

for i in range(len(seasonal_pacf_values)):
    seasonal_pacf_conf[i] = seasonal_pacf_conf[i] - seasonal_pacf_values[i]

seasonal_pacf_conf = pd.DataFrame(seasonal_pacf_conf, columns=['Upper', 'Lower'])

In [341]:
fig = go.Figure(go.Bar(
    y = seasonal_acf_values
))

fig.add_trace(go.Scatter(
    x = list(seasonal_acf_conf.index) + list(seasonal_acf_conf.index[::-1]),
    y = list(seasonal_acf_conf['Upper']) + list(seasonal_acf_conf['Lower'][::-1]),
    fill='toself',
    fillcolor='rgba(0,100,80,0.2)',
    line=dict(color='rgba(255,255,255,0)'),
    hoverinfo="skip",
    showlegend=False
))

fig.update_yaxes(title="Autocorrelation", range=[-1, 1])
fig.update_xaxes(title="Lag")

fig.show()

In [342]:
fig = go.Figure(go.Bar(
    y = seasonal_pacf_values
))

fig.add_trace(go.Scatter(
    x = list(seasonal_pacf_conf.index) + list(seasonal_pacf_conf.index[::-1]),
    y = list(seasonal_pacf_conf['Upper']) + list(seasonal_pacf_conf['Lower'][::-1]),
    fill='toself',
    fillcolor='rgba(0,100,80,0.2)',
    line=dict(color='rgba(255,255,255,0)'),
    hoverinfo="skip",
    showlegend=False
))

fig.update_yaxes(title="Partial Autocorrelation", range=[-1, 1])
fig.update_xaxes(title="Lag")

fig.show()

## SARIMA(4, 0, 0, 1, 0, 0, 24)

In [343]:
model2 = arimamodel(training_data=train_df['Generated Energy'], trend='c', p=1, d=0, q=0, P=6, D=1, Q=0, m=24)
print(model2.summary())

MemoryError: Unable to allocate 1.83 GiB for an array with shape (8616, 169, 169) and data type float64

In [ ]:
forecast2, conf_int2 = arima_forecast(data=gen_df, fitted_model=model2, start_index=0, end_index=validation_df.index[-1])
forecast2

In [ ]:
fig = go.Figure(go.Scattergl(
    x = train_df.index,
    y = train_df['Generated Energy'],
    name = "Training Data"
))

fig.add_trace(go.Scattergl(
    x = validation_df.index,
    y = validation_df['Generated Energy'],
    name = "Validation Data"
))

fig.add_trace(go.Scattergl(
    x = forecast2[validation_df.index[0]:validation_df.index[-1]].index,
    y = forecast2['Prediction'][validation_df.index[0]:validation_df.index[-1]],
    name = "Predicted Values"
))

# if bands == True:
#     fig.add_trace(go.Scattergl(
#         x = conf_int2.index,
#         y = conf_int2['lower Generated Energy'],
#         name = "Lower Bound"
#     ))
#
#     fig.add_trace(go.Scattergl(
#         x = conf_int2.index,
#         y = conf_int2['upper Generated Energy'],
#         name = "Upper Bound"
#     ))

fig.update_yaxes(title="Generated Energy [kWh]")

fig.show()

In [312]:
# model = SARIMAX(train_df['Generated Energy'], order=(1, 1, 0), seasonal_order=(0, 1, 3, 24))
# fitted_model = model.fit()
#
# t = fitted_model.forecast(8760, alpha=0.2)
#
# print(t)

In [313]:
#test_df['PV_PVInsolationHArray'].values.reshape(72, 1)

In [314]:
# import pmdarima as pm
#
# seasonal_model = pm.auto_arima(train_df[['Generated Energy']],
#                                #exogenous=train_df[['PV_PVInsolationHArray']],
#                                start_p=1, start_q=1, d=1,
#                                test='adf',
#                                max_p=3, max_q=3, m=24,
#                                start_P=0, start_Q=0, seasonal=True,
#                                max_P=2, max_Q=2,
#                                D=1, trace=True,
#                                error_action='ignore',
#                                suppress_warnings=True,
#                                stepwise=True)
#
# seasonal_model.summary()

### SARIMAX(?, ?, ?, ?, ?, ?, 24)

In [315]:
model = SARIMAX(train_df['Generated Energy'], exog=train_df['PV_PVInsolationHArray'], trend='c',
                 order=(1, 0, 0), seasonal_order=(1, 0, 0, 24))
model3 = model.fit()
print(model3.summary())

                                     SARIMAX Results                                      
Dep. Variable:                   Generated Energy   No. Observations:                 8616
Model:             SARIMAX(1, 0, 0)x(1, 0, 0, 24)   Log Likelihood                -131.482
Date:                            Mon, 02 May 2022   AIC                            272.965
Time:                                    11:28:34   BIC                            308.272
Sample:                                02-01-2015   HQIC                           285.005
                                     - 01-25-2016                                         
Covariance Type:                              opg                                         
                            coef    std err          z      P>|z|      [0.025      0.975]
-----------------------------------------------------------------------------------------
intercept                -0.0007      0.004     -0.156      0.876      -0.009       0.008
PV

In [316]:
gen_df['Prediction'] = model3.predict(start=0, end=validation_df.index[-1], exog=validation_df['PV_PVInsolationHArray'])
gen_df['Prediction']

Timestamp
2015-02-01 00:00:00    0.001350
2015-02-01 01:00:00    0.017074
2015-02-01 02:00:00    0.016257
2015-02-01 03:00:00    0.016543
2015-02-01 04:00:00    0.016720
                         ...   
2016-01-31 19:00:00         NaN
2016-01-31 20:00:00         NaN
2016-01-31 21:00:00         NaN
2016-01-31 22:00:00         NaN
2016-01-31 23:00:00         NaN
Freq: H, Name: Prediction, Length: 8760, dtype: float64

In [317]:
fig = go.Figure(go.Scattergl(
    x = train_df.index,
    y = train_df['Generated Energy'],
    name = "Training Data"
))

fig.add_trace(go.Scattergl(
    x = validation_df.index,
    y = validation_df['Generated Energy'],
    name = "Validation Data"
))

fig.add_trace(go.Scattergl(
    x = gen_df[validation_df.index[0]:validation_df.index[-1]].index,
    y = gen_df['Prediction'][validation_df.index[0]:validation_df.index[-1]],
    name = "Predicted Values"
))

# if bands == True:
#     fig.add_trace(go.Scattergl(
#         x = conf_interval.index,
#         y = conf_interval['lower Generated Energy'],
#         name = "Lower Bound"
#     ))
#
#     fig.add_trace(go.Scattergl(
#         x = conf_interval.index,
#         y = conf_interval['upper Generated Energy'],
#         name = "Upper Bound"
#     ))

fig.update_yaxes(title="Generated Energy [kWh]")

fig.show()

### Forecasting

In [318]:
# test = fitted_model.get_forecast(8760)
# yhat = test.predicted_mean
# yhat_conf = test.conf_int(alpha=0.9)
# yhat_conf

In [319]:
# fig = go.Figure(go.Scattergl(
#     x = gen_df.index,
#     y = gen_df['Generated Energy'],
#     name = "Observed Values"
# ))
#
# fig.add_trace(go.Scattergl(
#     x = gen_df.index,
#     y = gen_df['Prediction'],
#     name = "Predicted Values"
# ))
#
# # fig.add_trace(go.Scattergl(
# #     x = yhat_conf.index,
# #     y = yhat_conf['lower Generated Energy'],
# #     name = "Lower Bound"
# # ))
# #
# # fig.add_trace(go.Scattergl(
# #     x = yhat_conf.index,
# #     y = yhat_conf['upper Generated Energy'],
# #     name = "Upper Bound"
# #))
#
# fig.show()

### Future values

In [320]:
# If we need to predict future values

# from pandas.tseries.offsets import DateOffset
#
# new_dates = [gen_df.index[-1]+DateOffset(hours=x) for x in range(1, 26) ]
# new_dates

# gen_df_predict = pd.DataFrame(index=new_dates, columns=gen_df.columns)
# test_df = pd.concat([gen_df, gen_df_predict])
# test_df['Prediction'] = fitted_model.predict(start=8759, end=8785)
# test_df

In [326]:
X

Generated Energy  PV_PVInsolationHArray
Timestamp                                                   
2015-02-01 00:00:00          0.018496               0.057408
2015-02-01 01:00:00          0.018332               0.060286
2015-02-01 02:00:00          0.018385               0.058811
2015-02-01 03:00:00          0.018502               0.058865
2015-02-01 04:00:00          0.018524               0.059288
...                               ...                    ...
2016-01-28 19:00:00          0.017729               0.057850
2016-01-28 20:00:00          0.017849               0.056320
2016-01-28 21:00:00          0.017882               0.057342
2016-01-28 22:00:00          0.018000               0.057909
2016-01-28 23:00:00          0.018138               0.056369

[8688 rows x 2 columns]

In [327]:
np.corrcoef(X['Generated Energy'], X['PV_PVInsolationHArray'])[0, 1]**2

0.9478207764705181